In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.widgets import Slider
from ipywidgets import interact
import scipy.constants as const
# how to install all the packages that are missing?



In [2]:

# Configuración inicial
L = 1.0  # Longitud del pozo en nanómetros
n_max = 5  # Número máximo de estados a visualizar

# Función de onda para el pozo infinito
def psi_n(n, x, L):
    return np.sqrt(2/L) * np.sin(n * np.pi * x / L)

# Densidad de probabilidad
def probability_density(n, x, L):
    return np.abs(psi_n(n, x, L))**2

# Energía para cada estado
def energy_n(n, L, m=const.m_e):
    return (n**2 * const.h**2) / (8 * m * L**2 * 1e-18)  # Convertir a eV

# Crear la visualización
x = np.linspace(0, L, 100)

@interact(n=(1, n_max, 1))
def plot_wavefunction(n=1):
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(12, 4))
    
    # Función de onda
    ax1.plot(x, psi_n(n, x, L))
    ax1.set_title(f'Función de onda para n={n}')
    ax1.set_xlabel('Posición (nm)')
    ax1.set_ylabel('ψ_n(x)')
    ax1.grid(True)
    
    # Densidad de probabilidad
    ax2.plot(x, probability_density(n, x, L))
    ax2.set_title(f'Densidad de probabilidad para n={n}')
    ax2.set_xlabel('Posición (nm)')
    ax2.set_ylabel('|ψ_n(x)|²')
    ax2.grid(True)
    
    plt.tight_layout()
    plt.show()
    
    # Mostrar información de energía
    E_n = energy_n(n, L)
    print(f"Energía del estado n={n}: {E_n:.3f} eV")

interactive(children=(IntSlider(value=1, description='n', max=5, min=1), Output()), _dom_classes=('widget-inte…

In [3]:
from matplotlib.animation import FuncAnimation
from IPython.display import HTML


In [4]:

# Parámetros iniciales
n_components = 3  # Número de estados en la superposición
L = 1.0  # Longitud del pozo

# Coeficientes de superposición (pueden ser complejos)
coefficients = [0.6+0j, 0.8+0j, 0.5+0j]  # Ejemplo con 3 estados

# Normalizar los coeficientes
norm = np.sqrt(sum(np.abs(c)**2 for c in coefficients))
coefficients = [c/norm for c in coefficients]

# Función de onda en superposición en el tiempo t
def superposicion(x, t, coefficients, L):
    psi = np.zeros_like(x, dtype=complex)
    for n, c in enumerate(coefficients, 1):
        E_n = energy_n(n, L)
        psi += c * psi_n(n, x, L) * np.exp(-1j * E_n * t / const.hbar)
    return psi

# Crear animación
fig, ax = plt.subplots(figsize=(10, 6))
x = np.linspace(0, L, 1000)
t_values = np.linspace(0, 2e-15, 100)  # 2 femtosegundos

line, = ax.plot(x, np.zeros_like(x))
ax.set_xlim(0, L)
ax.set_ylim(-2, 2)
ax.set_xlabel('Posición (nm)')
ax.set_ylabel('ψ(x,t) (Parte Real)')
ax.set_title('Evolución temporal de una superposición de estados')
ax.grid(True)

def init():
    line.set_data([], [])
    return line,

def animate(i):
    t = t_values[i]
    psi_t = superposicion(x, t, coefficients, L)
    line.set_data(x, np.real(psi_t))
    return line,

ani = FuncAnimation(fig, animate, frames=len(t_values),
                    init_func=init, blit=True, interval=50)

plt.close(fig)  # Evita que se muestre el plot estático
HTML(ani.to_jshtml())

In [ ]:
from scipy.special import sph_harm, assoc_laguerre
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import math

# Función de onda hidrogenoide (parte radial)
def R_nl(n, l, r, a0=0.529):  # a0 en Angstroms
    
    rho = 2 * r / (n * a0)
    norm = np.sqrt((2/(n*a0))**3 * math.factorial(n-l-1)/(2*n*math.factorial(n+l)))
    laguerre = assoc_laguerre(rho, n-l-1, 2*l+1)
    return norm * np.exp(-rho/2) * rho**l * laguerre

# Función de onda completa
def psi_hydrogen(n, l, m, r, theta, phi, a0=0.529):
    radial = R_nl(n, l, r, a0)
    angular = sph_harm(m, l, phi, theta)
    return radial * angular

# Crear una malla 3D
def create_mesh(n, l, m, size=100, a0=0.529):
    # Crear coordenadas esféricas
    r = np.linspace(0, 5*a0*n**2, size)  # Radio hasta ~5 veces el radio esperado
    theta = np.linspace(0, np.pi, size)
    phi = np.linspace(0, 2*np.pi, size)
    
    R, Theta, Phi = np.meshgrid(r, theta, phi, indexing='ij')
    
    # Calcular la función de onda
    psi = psi_hydrogen(n, l, m, R, Theta, Phi, a0)
    
    # Convertir a coordenadas cartesianas para visualización
    x = R * np.sin(Theta) * np.cos(Phi)
    y = R * np.sin(Theta) * np.sin(Phi)
    z = R * np.cos(Theta)
    
    return x, y, z, np.abs(psi)**2

# Visualización interactiva de orbitales
@interact(n=(1, 4, 1), l=(0, 3, 1), m=(-3, 3, 1))
def plot_orbital(n=1, l=0, m=0):
    if l >= n:
        print("Error: l debe ser menor que n")
        return
    if abs(m) > l:
        print("Error: |m| debe ser ≤ l")
        return
    
    x, y, z, density = create_mesh(n, l, m, size=50)
    
    # Encontrar la superficie de densidad constante
    fig = plt.figure(figsize=(10, 8))
    ax = fig.add_subplot(111, projection='3d')
    
    # Usar un valor de isosuperficie que capture la mayor parte de la densidad de probabilidad
    level = 0.5 * np.max(density)
    
    # Visualizar la superficie
    ax.scatter(x, y, z, c=density.flatten(), cmap='viridis', alpha=0.3, s=1)
    ax.set_title(f'Orbital {n}{["s","p","d","f"][l]}{m} del átomo de hidrógeno')
    ax.set_xlabel('x (Å)')
    ax.set_ylabel('y (Å)')
    ax.set_zlabel('z (Å)')
    
    plt.show()

interactive(children=(IntSlider(value=1, description='n', max=4, min=1), IntSlider(value=0, description='l', m…